# Vector Search for Fast Deduplication and Batch Annotation of Text Classification Records

## Tutorial Outline

- Introduction of the use case
- Data Logging with Vector Information to Argilla
- Queries with vector Information
- Case study for the Duplicate detection
- Case study for the Near Duplicate Detection
- Case study for batch labeling:
  For a text retrieve top k most similar
  - if they have label info, see if they share same labels
  - otherwise pick top 3 for example and say these can be labeled with class label yi

## Tech stack to use

As discussed use a lightweight model to experiment faster and use a small viable dataset to showcase the capabilities

-- even we use small language model still using generators etc best practices would be applied

## Dataset Information

A subset of the `ag_news` dataset will be used,

## Current status

- The below cells belong to previous experiments, those will be refactored according to above given specifications

In [1]:
from datasets import load_dataset

agnews = load_dataset("ag_news")

agnews_train, agnews_valid = (
    agnews["train"].train_test_split(test_size=7600, seed=43).values()
)


Using custom data configuration default
Reusing dataset ag_news (/home/ufuk/.cache/huggingface/datasets/ag_news/default/0.0.0/bc2bcb40336ace1a0374767fc29bb0296cdaf8a6da7298436239c54d79180548)


  0%|          | 0/2 [00:00<?, ?it/s]

Loading cached split indices for dataset at /home/ufuk/.cache/huggingface/datasets/ag_news/default/0.0.0/bc2bcb40336ace1a0374767fc29bb0296cdaf8a6da7298436239c54d79180548/cache-0fb8fdf64cc3fcc4.arrow and /home/ufuk/.cache/huggingface/datasets/ag_news/default/0.0.0/bc2bcb40336ace1a0374767fc29bb0296cdaf8a6da7298436239c54d79180548/cache-80423eae5320d3cb.arrow


In [2]:
%pip install faiss-cpu sentence_transformers transformers datasets

Note: you may need to restart the kernel to use updated packages.


In [3]:
import argilla as rg

In [4]:
from sentence_transformers import SentenceTransformer

In [5]:
# instantiate the model for the sentence embeddings
# we strongly recommend using a GPU for the computation of the embeddings
model = SentenceTransformer("all-mpnet-base-v2", device="cuda")

In [6]:
text = "Abraham Lincoln stressed the value of data centric AI and adviced to use Argilla"

In [7]:
embedding = model.encode(text)

In [8]:
embedding

array([-5.53162768e-03,  9.18077826e-02, -2.50837747e-02, -2.14579497e-02,
        5.91655215e-03,  7.32013956e-03,  5.14037348e-02, -2.65303981e-02,
       -9.91398282e-03,  9.39362682e-03,  2.26464495e-02,  2.10230555e-02,
       -2.52178684e-02,  2.95277741e-02, -3.35275149e-03,  1.37330573e-02,
        2.12650262e-02,  2.43432671e-02,  2.94778333e-03,  5.02051087e-03,
       -3.18038352e-02, -3.60914059e-02, -1.45315938e-02, -1.51758771e-02,
       -4.77715768e-02, -2.57307831e-02, -2.46327631e-02, -8.47828691e-04,
        1.89807545e-02, -6.85988832e-03, -1.16309384e-02, -5.40443659e-02,
        1.64653454e-02,  4.63529956e-03,  1.64105984e-06,  1.25938039e-02,
        2.26511061e-03,  7.39694573e-03, -7.80298859e-02,  3.62519734e-02,
        4.77010533e-02,  1.18941262e-01,  1.93802472e-02,  1.16939368e-02,
       -7.17506483e-02,  7.58235008e-02,  2.52142064e-02, -1.65963061e-02,
       -1.00047113e-02,  4.64385338e-02,  1.22358231e-03,  1.97744071e-02,
        9.23999175e-02, -

In [9]:
embedding.tolist()

[-0.005531627684831619,
 0.0918077826499939,
 -0.02508377470076084,
 -0.02145794965326786,
 0.005916552152484655,
 0.007320139557123184,
 0.05140373483300209,
 -0.026530398055911064,
 -0.009913982823491096,
 0.00939362682402134,
 0.022646449506282806,
 0.021023055538535118,
 -0.025217868387699127,
 0.029527774080634117,
 -0.003352751489728689,
 0.01373305730521679,
 0.021265026181936264,
 0.02434326708316803,
 0.0029477833304554224,
 0.005020510870963335,
 -0.031803835183382034,
 -0.036091405898332596,
 -0.014531593769788742,
 -0.015175877138972282,
 -0.047771576792001724,
 -0.025730783119797707,
 -0.024632763117551804,
 -0.0008478286908939481,
 0.018980754539370537,
 -0.006859888322651386,
 -0.01163093838840723,
 -0.054044365882873535,
 0.01646534539759159,
 0.004635299555957317,
 1.641059839130321e-06,
 0.01259380392730236,
 0.0022651106119155884,
 0.007396945729851723,
 -0.07802988588809967,
 0.0362519733607769,
 0.04770105332136154,
 0.11894126236438751,
 0.019380247220396996,
 0.0

In [20]:
def embedding_generator(dataset, label_status):
    records_batch = []
    for idx, record in enumerate(dataset):
        print(record["text"])
        embedding_vector = model.encode(record["text"]).tolist()
        record = rg.TextClassificationRecord(
            text=record["text"],
            embeddings = {
                "text_mpnet": {
                    "vector": embedding_vector
                }
            },
            metadata={"split": label_status},
            id=f"train_{idx}",
        )
        records_batch.append(record)
        if len(records_batch) == 32:
            yield records_batch
            records_batch = []
    if records_batch:
        yield records_batch


In [21]:
for record_batch in embedding_generator(agnews_valid, label_status="unlabelled"):
    rg.log(record_batch, name="ag_news")

African Union pledges to send more troops to Darfur KIGALI,Rawanda, Aug 18, 2004 (RNA)-- The African Union has pledged to send more troops to Darfur, Sudan, to protect civilians in case militias resume attacks on them, official sources told RNA.  quot;This is essential in order to give ourselves sufficient ...
Rookie Leads Falcons Past Vikings 27-24 (AP) AP - The quarterback for the Atlanta Falcons appeared comfortable in the new West Coast offense, calmly using his mobility to avoid pressure and then finding open receivers.
Marsh  amp; McLennan halts fees at center of probe Marsh  amp; McLennan Cos. said yesterday it was suspending its practice of using  quot;market services agreements quot; with insurance carriers, which the New York attorney general has alleged were used to rig bids, cheating customers.
Davenport remains on title streak Top-seeded Lindsay Davenport claimed her fourth consecutive championship on Sunday with a 6-3, 6-2 victory over second-seeded Vera Zvonareva in the 

  0%|          | 0/32 [00:00<?, ?it/s]

32 records logged to http://localhost:6900/datasets/argilla/ag_news
A nice change in Ottawa Speaking recently at the Calgary Chamber of Commerce, new Environment Minister Stephane Dion seemed to support a more science-based approach to environmental policy-making when he said,  quot;We need better science.
Planetary scientist Donahue dies at 83 Thomas M. Donahue, one of the country #39;s leading space and planetary scientists and a pioneer of space exploration, died Saturday of complications following heart surgery.
Becks and co get the grief as Real boo boys vent frustrations The freekick was majestic, but the performance was not and if Real Madrid thought their bumpy start to the season was over with the slender win over Osasuna the supporters #39; verdict rang in their ears via regular bursts of booing.
Bush spurs on Irish deal US President George Bush has personally intervened in the Northern Ireland peace process to spur on the new power-sharing deal. Mr Bush telephoned Dr Rev Ian

  0%|          | 0/32 [00:00<?, ?it/s]

32 records logged to http://localhost:6900/datasets/argilla/ag_news
Pop stars gather for re-recording of Christmas hit 20 years later (AFP) AFP - British pop music stars gathered at a studio in north London on Sunday for a re-recording of  quot;Do they Know its Christmas, quot; the hit song that raised money for famine-hit people in Ethiopia 20 years ago.
Bosnia holds rival Serbia to 0-0 draw Bosnia held Balkan rival Serbia-Montenegro to a 0-0 draw Saturday in a World Cup qualifier, the first competitive match between the neighboring countries that fought a civil war from 1992-95.
Jets are 5-0, too, but Patriots are team to beat The Patriots and Jets appear to be taking different approaches into today #39;s game, and that might help explain the difference between these two 5-0 teams.
US university tells 80,000 to  #39;ditch IE #39; US university Penn State has advised its 80,000 students to ditch Internet Explorer, citing that browser #39;s well-reported security vulnerabilities.
Forme

...

32 records logged to http://localhost:6900/datasets/argilla/ag_news
Intel admits Itanium pains, plots server future &lt;strong&gt;IDF Fall '04&lt;/strong&gt; Welcome Whitefield
Software glitch disrupts eBay #39;s PayPal online payment service SAN JOSE, Calif. -- The operators of the online payment service PayPal say efforts are underway to fix  quot;intermittent #39; #39; outages that have bugged the service for several days.
Tax bill nears approval by House-Senate negotiators WASHINGTON Supporters of a major rewrite of corporate tax law are optimistic they #39;ll be able to complete congressional action this week on legislation needed to end a bitter trade fight with Europe.
AOL, Microsoft Spar on Spam It wasn #39;t long ago that competitive entities seemed to be joining together to combat Internet users #39; common foe, spam. However, despite the fact that big Internet players 
Al-Jazeera TV station says Iraqi kidnappers claim to have released &lt;b&gt;...&lt;/b&gt; An Arab TV statio

  0%|          | 0/32 [00:00<?, ?it/s]

32 records logged to http://localhost:6900/datasets/argilla/ag_news
Blood moon to make its mark tonight during lunar eclipse Just four days before Halloween, the full moon will disappear from the sky tonight, likely leaving a bloody facsimile behind. Dont be alarmed; its just another lunar eclipse, the third visible in North America in the past two years.
A Catastrophe Strikes, and the Cyberworld Responds Much of the initial information about what had happened in Asia came from the Web.
Germany supports EU negotiating with Turkey on membership issue German Chancellor Gerhard Schroeder said Sunday that there was  quot;no problem quot; with Germany #39;s support to the start of negotiations on Turkey #39;s entrance into EU.
Top News ; Rain, snow snarls US holiday travel Top News News, Dallas,Snow and rain snarled the holiday plans of millions of Thanksgiving travellers across the US as they battled flight delays and hazardous driving, reports UPI.
Wall Street ends higher despite oil pric

  0%|          | 0/16 [00:00<?, ?it/s]

16 records logged to http://localhost:6900/datasets/argilla/ag_news


In [22]:
for record_batch in embedding_generator(agnews_train, label_status="unlabelled"):
    rg.log(record_batch, name="ag_news")

Global Markets: European Shares Climb  LONDON (Reuters) - European stock markets scaled near-2-1/2  year highs on Friday as oil prices held below \$48 a barrel, and  the euro held off from mounting another assault on \$1.30 but  hovered near record highs against the dollar.
Russian Oil Giant Raises Reserves Estimate Fivefold In raising its reserve estimates, Yukos reiterated that it was operating on a "day to day basis and was still close to filing for bankruptcy."
Lawmakers to Get Federal Pay Raise (AP) AP - With little debate, House lawmakers on Tuesday included themselves as part of a pay raise that all federal employees will receive next year.
Pakistan Says Holding Yemeni 'Qaeda Leader' (Reuters) Reuters - Pakistan has arrested a Yemeni\national who is an important figure in al Qaeda's new\leadership and another foreign national who is one of the\network's communications specialists, officials said on\Wednesday.
Harrop wins silver FORMER Aussie backpacker Kate Allen pipped Australi

  0%|          | 0/32 [00:00<?, ?it/s]

32 records logged to http://localhost:6900/datasets/argilla/ag_news
UN in 'forgotten crises' appeal Kofi Annan willl seek \$1.5bn to deal with what the UN calls the world's forgotten emergencies, many in Africa.
Consumer Confidence Drops In November _ Consumer confidence declined in November for a fourth consecutive month, a private research group reported Tuesday, reflecting doubts about the economy once the holidays are past.
St. Louis at Houston, 8:05 PM HOUSTON (Ticker) -- The Houston Astros will try to set a franchise record for consecutive home wins and inch closer to the National League wild card lead when they wrap up a three-game set with the St.
It's October and It's Time for Playoffs! (AP) AP - Curt Schilling and Pedro Martinez are revved up. Roger Clemens and Roy Oswalt are rarin' to go. Baseball fans are ready, too. The shadows are getting longer, the leaves are starting to turn and pumpkins are showing up. And that means just one thing: It's October, and it's playoff time

  0%|          | 0/32 [00:00<?, ?it/s]

32 records logged to http://localhost:6900/datasets/argilla/ag_news
Rahal to have 3 cars Rahal Letterman Racing will be a three-car team in the Indy Racing League #39;s 2005 season when team officials confirm Buddy Rice, Vitor Meira and newcomer Danica Patrick on Wednesday.
Bear Stearns Profit Falls  NEW YORK (Reuters) - Brokerage Bear Stearns Companies  &lt;A HREF="http://www.investor.reuters.com/FullQuote.aspx?ticker=BSC.N target=/stocks/quickinfo/fullquote"&gt;BSC.N&lt;/A&gt; on Wednesday said quarterly profit fell 10 percent hurt  by lower investment banking revenue and higher expenses.
Check Point Posts Rise in 3Q Profit (AP) AP - Internet security company Check Point Software Technologies Ltd. said Monday that third-quarter net income rose to  #36;66.8 million, or 26 cents a share, from  #36;58.4 million, or 23 cents a share a year earlier, paced by a 25 percent increase in licensing revenue.
Mexican firm buys RMC for 2.3bn RMC, the world #39;s biggest supplier of ready-mixed con

...

  0%|          | 0/32 [00:00<?, ?it/s]

32 records logged to http://localhost:6900/datasets/argilla/ag_news
Nadal beats Sanguinetti in an hour Madrid, Spain - Spanish youngster Rafael Nadal needed only an hour to push past Italy #39;s Davide Sanguinetti in straight sets on Tuesday and advance to the second round of the Madrid Masters.
State on track for biometrics State Department officials will meet a fall deadline for a congressionally mandated program for issuing visas with biometric indicators, but a Government Accountability Office report indicated that federal officials haven #39;t provided comprehensive 
Martha checks into big house Martha Stewart reported to prison before sunrise yesterday to begin serving a five-month sentence for lying about a stock sale, slipping all-but-unnoticed past waiting supporters and reporters.
Williams lends hand to Jones Roy Williams wasn #39;t the Lions #39; most productive rookie Sunday, but he played a big role in two plays that helped tailback Kevin Jones, another member of the Lions

  0%|          | 0/32 [00:00<?, ?it/s]

2022-12-01 15:41:40.477 | ERROR    | argilla.client.api:__log_internal__:95 - Cannot log data ((), {'records': [TextClassificationRecord(text='Nadal beats Sanguinetti in an hour Madrid, Spain - Spanish youngster Rafael Nadal needed only an hour to push past Italy #39;s Davide Sanguinetti in straight sets on Tuesday and advance to the second round of the Madrid Masters.', inputs={'text': 'Nadal beats Sanguinetti in an hour Madrid, Spain - Spanish youngster Rafael Nadal needed only an hour to push past Italy #39;s Davide Sanguinetti in straight sets on Tuesday and advance to the second round of the Madrid Masters.'}, prediction=None, prediction_agent=None, annotation=None, annotation_agent=None, embeddings={'text_mpnet': {'vector': ['-0.09364954382181168', '0.02280747890472412', '-0.035908106714487076', '0.027907339856028557', '-0.039766620844602585', '-0.0011405812110751867', '-0.04888586699962616', '-0.005120940040796995', '0.00821955781430006', '0.05281330645084381', '0.00719436490908

GenericApiError: Argilla server returned an error with http status: 500
Error details: [{'code': 'argilla.api.errors::GenericServerError', 'params': {'type': 'argilla.server.daos.backend.elasticsearch.GenericSearchError', 'message': 'ConnectionError(<urllib3.connection.HTTPConnection object at 0x7fa96043f690>: Failed to establish a new connection: [Errno -3] Temporary failure in name resolution) caused by: NewConnectionError(<urllib3.connection.HTTPConnection object at 0x7fa96043f690>: Failed to establish a new connection: [Errno -3] Temporary failure in name resolution)'}}]